In [1]:
import pycbc
from pycbc.waveform import get_fd_waveform, get_td_waveform
from pycbc.filter import match, sigmasq
from pycbc import conversions,psd

In [2]:
import time, h5py, sys, numpy as np
from tqdm import tqdm
import uuid
import pandas as pd
from multiprocessing import Pool

# Read in the bank

In [3]:
four = h5py.File('./4ogcbank/combined.hdf','r')

# PSD 

In [4]:
# read in PSD
psdtxt = np.loadtxt('/work/yifan.wang/search-config/highspin/bank/o3psd.txt')

length = len(psdtxt[:,0])
delta_f = psdtxt[1,0] - psdtxt[0,0]
flow = 15

psd = pycbc.psd.read.from_txt('/work/yifan.wang/search-config/highspin/bank/o3psd.txt',
                             length,
                             delta_f,
                             flow,
                             is_asd_file=False)

In [5]:
length, delta_f

(16385, 0.125)

In [6]:
from pycbc import distributions
dist = distributions.Uniform(injmass1=(1,5), injmass2=(1,2),
                             injspin1z=(-0.95,0.95),injspin2z=(-0.95,0.95))

In [7]:
def save_output(injpar,output):
    '''
    save the output as a csv file
    
    Parameters
    -----------
    injpar: dict
        injection parameters
    outpar: dict
        max_match parameters
    '''
    df1 = pd.DataFrame.from_dict(injpar)
    df2 = pd.DataFrame.from_dict(output)
    df3 = df1.join(df2)
    df3.to_csv('match-'+str(uuid.uuid4())[:8]+'.csv')
    
# calculate fitting factors
def fitting_factor(inj_sample, base_bank=four, psd=psd,
                   flow=20, fhigh=1024,df=0.125,tau_tol=1):
    '''
    Parameters:
    -----------
    inj_sample: injections, should at least contain mass1,mass2,spin1z,spin2z
    base_bank: The bank to be verified
    psd: PSD curve
    
    '''
    base_bank_tau0 = conversions.tau0_from_mass1_mass2(
                                            mass1=base_bank['mass1'][:],
                                            mass2=base_bank['mass2'][:],
                                            f_lower=flow)
    out_par = {} # returned object
    for k in range(len(inj_sample)):#loop over all injection samples
        hpinj, _ = get_fd_waveform(approximant="TaylorF2",
                           mass1=inj_sample['injmass1'][k],
                           mass2=inj_sample['injmass2'][k],
                           spin1z=inj_sample['injspin1z'][k],
                           spin2z=inj_sample['injspin2z'][k],
                           delta_f=df,
                           f_lower=flow,
                           f_final=fhigh)#injection waveform

        inj_tau0 = conversions.tau0_from_mass1_mass2(
                                           mass1=inj_sample['injmass1'][k],
                                           mass2=inj_sample['injmass2'][k],
                                           f_lower=flow)# injection waveform duration
        
        #select those in the bank close to the injection waveform
        index = np.where( np.abs(inj_tau0 - base_bank_tau0) < tau_tol )[0]

        max_match = 0 
        max_par = {} #initialization
    
        for i in tqdm(index):
            # extract the base bank parameters
            par = {}
            for k in base_bank:
                par[k] = base_bank[k][i]
            par.pop('approximant')
            par.pop('f_lower')
            
            #template waveform
            hpbank, __ = get_fd_waveform(approximant = "TaylorF2",
                                     **par,
                                     delta_f=df,
                                     f_lower=flow,
                                     f_final=fhigh)
            #calculate fitting factor
            cache_match, _ = match(hpinj,
                               hpbank,
                               psd = psd,
                               low_frequency_cutoff = flow,
                               high_frequency_cutoff = fhigh)
            
            #save the maximized fitting factor
            if cache_match > max_match:
                max_match = cache_match
                max_par = par 
        
        #save everything in a single dict, merge max_match into max_par
        max_par['max_match'] = max_match 
        
        # initialization
        if len(out_par) == 0:
            for k in max_par.keys():
                out_par[k] = [] 
        # append results in a dict
        for k in max_par.keys():
            out_par[k].append(max_par[k]) 
    
    save_output(inj_sample, out_par)

In [8]:
samples = []
for j in range(30):
    samples.append(dist.rvs(30))

In [9]:
samples

[array([(1.05938142, 1.07299188, -0.86772177, -0.02731187),
        (4.98580318, 1.88478787, -0.87965973,  0.17073561),
        (1.22704639, 1.30344771,  0.82207267, -0.51154447),
        (2.93938694, 1.60013003, -0.6857442 , -0.28953605),
        (3.49554358, 1.15657846,  0.34208836, -0.59653601),
        (1.93352342, 1.50694749,  0.24794627, -0.7642975 ),
        (2.03927953, 1.81760493, -0.38205461, -0.59779068),
        (1.03975335, 1.19476436, -0.05176321, -0.16585469),
        (2.41394913, 1.28453947, -0.05386284,  0.86600869),
        (4.21509822, 1.07897049, -0.00403493, -0.69389326),
        (3.8244724 , 1.061953  ,  0.08323539, -0.15140033),
        (3.2788893 , 1.57693949, -0.53913435, -0.00719218),
        (1.98783892, 1.45693149, -0.75914221, -0.06536193),
        (1.40886144, 1.62618489,  0.12337446, -0.36478086),
        (1.79431984, 1.14742832, -0.74133842, -0.75262099),
        (4.16637018, 1.38857691, -0.08096391, -0.73960042),
        (1.5591444 , 1.64556989, -0.6655

In [ ]:
p = Pool(30)
ds = p.map(fitting_factor, samples)

 64%|██████████████████████████████████████████████████████████████▌                                   | 2418/3784 [14:44<08:41,  2.62it/s]


 27%|██████████████████████████▏                                                                       | 1996/7476 [08:49<21:23,  4.27it/s]


 13%|█████████████▏                                                                                    | 1055/7836 [04:36<39:39,  2.85it/s]


 14%|█████████████▌                                                                                 | 1628/11432 [08:18<1:15:00,  2.18it/s]


 91%|█████████████████████████████████████████████████████████████████████████████████████████▏        | 5538/6086 [31:05<02:18,  3.97it/s]


 94%|████████████████████████████████████████████████████████████████████████████████████████▋     | 14512/15386 [1:18:21<03:30,  4.15it/s]


 86%|██████████████████████████████████████████████████████████████████████████████████▊             | 10827/12556 [58:44<09:13,  3.12it/s]


 90%|████████████████████████████████████████████████████████████████████████████████████▎         | 14538/16217 [1:21:36<09:46,  2.86it/s]


 42%|█████████████████████████████████████████▏                                                       | 5265/12415 [28:57<51:10,  2.33it/s]